# 1: Project Goal-> Text Classification
#### To predict the artist from a piece of lyrics/text provided 

In [206]:
# Reading libraries

import requests
import re
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import json
from itertools import chain

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import  MultinomialNB
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, confusion_matrix, f1_score
from imblearn.under_sampling import RandomUnderSampler, NearMiss

# 2: Extracting Song Lyrics from Webpage

### 2.1 Selecting artists/ albums and downloading their html code
* This is done to extract the links of the songs under the artist/ album to ultimately extract the lyrics

In [28]:
# assigning links of the different artists
Chet_Faker_URL = "https://www.lyrics.com/album/2902354/Built-on-Glass"
Tom_Odell_URL = "https://www.lyrics.com/album/3708199/Jubilee-Road"
KSI_URL = "https://www.lyrics.com/album/3815148/New-Age"
Cold_Play_URL = "https://www.lyrics.com/album/3734208/Live-in-Buenos-Aires-Live-in-S%C3%A3o-Paulo-A-Head-Full-of-Dreams"
Eminem_URL = "https://www.lyrics.com/album/3712659/Kamikaze"
URL = {"chet faker":Chet_Faker_URL,"tom odell":Tom_Odell_URL,"ksi":KSI_URL,"cold play":Cold_Play_URL,"eminem":Eminem_URL}

In [31]:
###### downloading the html files for the below artists
# for artist,link in URL.items():
#         page = requests.get(link)
#         f = open(artist+".txt","w")
#         f.write(page.text)
#         f.close()

### 2.2 Extracting the song links for each artist
* This is done to then use the song links to extract html code

In [33]:
# opening and reading each text file and grabbing the links to songs in a dictionary format
artist_song_link = {}

for artist,link in URL.items():
    f = open(artist+".txt","r")
    pattern = "<strong><a\shref\S\S(/lyric[^>]+\w)"
    artist_song_link[artist] = re.findall(pattern, f.read())
    f.close()

In [34]:
artist_song_link

{'chet faker': ['/lyric/32650524/Release+Your+Problems',
  '/lyric/32650523/Talk+Is+Cheap',
  '/lyric/30667573/No+Advice+%5BAirport+Version%5D+%5BVersion%5D',
  '/lyric/32650521/Melt',
  '/lyric/32650520/Gold',
  '/lyric/32650519/To+Me',
  '/lyric/32650517/Blush',
  '/lyric/32650516/1998',
  '/lyric/32650515/Cigarettes+%26+Loneliness',
  '/lyric/32650513/Dead+Body'],
 'tom odell': ['/lyric/35596899/Son+of+an+Only+Child',
  '/lyric/35596900/You%27re+Gonna+Break+My+Heart+Tonight',
  '/lyric/35596901/China+Dolls',
  '/lyric/35596902/Queen+of+Diamonds',
  '/lyric/35596903/Half+as+Good+as+You',
  '/lyric/35596904/Go+Tell+Her+Now',
  '/lyric/35596905/Don%27t+Belong+in+Hollywood',
  '/lyric/35596906/Wedding+Day',
  '/lyric/35596907/If+You+Wanna+Love+Somebody'],
 'ksi': ['/lyric/36161175/New+Age',
  '/lyric/36161174/Beerus',
  '/lyric/36161171/Real+Name',
  '/lyric/36161177/Pull+Up'],
 'cold play': ['/lyric/35581276/God+Put+a+Smile+Upon+Your+Face',
  '/lyric/35581255/Yellow',
  '/lyric/3558125

In [39]:
# complete the song link URL
initial_URL = "https://www.lyrics.com"
for artist,link in artist_song_link.items():
    for i in range(len(link)):
       artist_song_link[artist][i] = initial_URL+link[i]
        
    

In [40]:
artist_song_link

{'chet faker': ['https://www.lyrics.com/lyric/32650524/Release+Your+Problems',
  'https://www.lyrics.com/lyric/32650523/Talk+Is+Cheap',
  'https://www.lyrics.com/lyric/30667573/No+Advice+%5BAirport+Version%5D+%5BVersion%5D',
  'https://www.lyrics.com/lyric/32650521/Melt',
  'https://www.lyrics.com/lyric/32650520/Gold',
  'https://www.lyrics.com/lyric/32650519/To+Me',
  'https://www.lyrics.com/lyric/32650517/Blush',
  'https://www.lyrics.com/lyric/32650516/1998',
  'https://www.lyrics.com/lyric/32650515/Cigarettes+%26+Loneliness',
  'https://www.lyrics.com/lyric/32650513/Dead+Body'],
 'tom odell': ['https://www.lyrics.com/lyric/35596899/Son+of+an+Only+Child',
  'https://www.lyrics.com/lyric/35596900/You%27re+Gonna+Break+My+Heart+Tonight',
  'https://www.lyrics.com/lyric/35596901/China+Dolls',
  'https://www.lyrics.com/lyric/35596902/Queen+of+Diamonds',
  'https://www.lyrics.com/lyric/35596903/Half+as+Good+as+You',
  'https://www.lyrics.com/lyric/35596904/Go+Tell+Her+Now',
  'https://www

### 2.3 Downloading the lyrics page html for each artist's song
* This is done to then use the html to extract the lyrics from the html code

In [44]:
#downloading html and storing in list
# artist_lyric_html = {}

# for artist,link in artist_song_link.items():
#     song_html = []
#     for i in range(len(link)):
#         song_html.append(requests.get(artist_song_link[artist][i]).text)
#     artist_lyric_html[artist] = song_html

In [45]:
artist_lyric_html

{'chet faker': ['\n<!doctype html>\n<!--[if lt IE 7]> <html class="no-js lt-ie9 lt-ie8 lt-ie7" lang="en"> <![endif]-->\n<!--[if IE 7]>    <html class="no-js lt-ie9 lt-ie8" lang="en"> <![endif]-->\n<!--[if IE 8]>    <html class="no-js lt-ie9" lang="en"> <![endif]-->\n<!--[if gt IE 8]><!--> <html class="no-js" lang="en"> <!--<![endif]--><head>\n<meta charset="utf-8">\n<meta http-equiv="X-UA-Compatible" content="IE=edge,chrome=1">\n<title>Release Your Problems Lyrics</title>\n<meta name="description" content="Lyrics to Release Your Problems by Chet Faker from the Built on Glass album - including song video, artist biography, translations and more!">\n<meta name="keywords" content="Release Your Problems lyrics, lyrics for Release Your Problems, Release Your Problems song, Release Your Problems words, lyrics from Built on Glass">\n\t<meta name="viewport" content="width=device-width">\n<base href="https://www.lyrics.com/">\n\n<script>s4Prefix=\'https://static.stands4.com\';version=\'1.3.31\'

In [56]:
#storing dictionary data in json file
# f = open("Allartistsongs.json", "w")
# json.dump(artist_lyric_html,f)
# f.close()

In [104]:
# reading the json file which has html code for each song
f = open("Allartistsongs.json", "r")
songs_html = eval(f.read())
f.close()

### 2.4 Extracting the lyrics from the html code and cleaning them
* Cleaning means making the letters lower case and removing punctuation marks

In [215]:
all_artist_lyric = {}
for artist,link in songs_html.items():
    artist_lyric = []
    for i in range(len(link)):
        #songs_list = []
        songs_soup = BeautifulSoup(songs_html[artist][i],'html.parser')
        songs_list = songs_soup.find_all("pre",attrs={"class":"lyric-body"})[0].text.split("\n")
        songs_list = [i for i in songs_list if i != ""]
        artist_lyric.append(songs_list)
    all_artist_lyric[artist] = list(artist_lyric)
        

In [216]:
all_artist_lyric["eminem"][4].clear()
all_artist_lyric["eminem"][15].clear()

In [217]:
len(all_artist_lyric["chet faker"][0]) + len(all_artist_lyric["chet faker"][1])+ len(all_artist_lyric["chet faker"][2])+ len(all_artist_lyric["chet faker"][3])+ len(all_artist_lyric["chet faker"][4])+ len(all_artist_lyric["chet faker"][5])+ len(all_artist_lyric["chet faker"][6])+ len(all_artist_lyric["chet faker"][7])+ len(all_artist_lyric["chet faker"][8])+ len(all_artist_lyric["chet faker"][9])

300

In [218]:
#cleaning up lines so that there are no punctuation marks and everything is lowercase
all_lyric = {}
pattern = r"[^\w\s\d]"

for artist,link in all_artist_lyric.items():
    all_artist_lyric_cleaned = []
    for i in range(len(link)):
        for j in range(len(all_artist_lyric[artist][i])):
            cleaned = re.sub(pattern,' ',all_artist_lyric[artist][i][j].lower())
            all_artist_lyric_cleaned.append(cleaned)
    all_lyric[artist] = all_artist_lyric_cleaned

In [219]:
all_lyric

{'chet faker': ['won t you take it all on own',
  'you feeding something make me start to see in the night',
  'won t you help me roll back home',
  'the feet are stumbling  walking down the street in the light',
  'walk on the die',
  'i will never know',
  'lone with mind  won t take my',
  'eyes to see the break in your way',
  'release your problems ',
  'release your problems',
  'release your problems',
  'lone with mind  won t take my',
  'eyes to see the break in your way',
  'release your problems',
  'release your problems',
  'release your problems',
  'feels down you wore it by your',
  'i ve been poisoned reach around the streets and open fire',
  'feels a lot don t leave the light on',
  'i could be the warmest soul if i like',
  'what a night',
  'what a night',
  'what a night',
  'don t lie to my face',
  'oh so  your weak rhyme',
  'you doubt i bother reading into it',
  'i ll probably won t',
  'left to my own devices',
  'but that s the difference in our opinions',


### 2.5 Converting to Data Frame format
* So that each line of lyric can be assigned to the artist and is visible
* For easy use in train-test split

In [220]:
lyric_df = pd.DataFrame.from_dict(all_lyric,orient="index")
lyric_df.index.name = "artist"
lyric_df.reset_index(inplace=True)
lyric_df_melt = lyric_df.melt(id_vars="artist",var_name="index",value_name="lyric")
lyric_df_melt.drop("index",axis=1,inplace=True)
lyric_df_melt = lyric_df_melt[lyric_df_melt["lyric"].notnull()]
lyric_df_melt.reset_index(inplace=True)
lyric_df_melt.drop("index",axis=1,inplace=True)
lyric_df_melt

artist                                              lyric
0     chet faker                       won t you take it all on own
1      tom odell               ripples in my soup s got me dreaming
2            ksi  yeah  they can t hold us back  we on another l...
3      cold play                       where do we go nobody knows 
4         eminem  yeah  yo i m just gonna write down my first th...
...          ...                                                ...
2810      eminem                         ever gonna slow up and i m
2811      eminem                       ready to snap any moment i m
2812      eminem                   thinkin  it s time to go get  em
2813      eminem                 they ain t gonna know what hit  em
2814      eminem                    w w when they get bit with the 

[2815 rows x 2 columns]

In [221]:
lyric_df_melt["artist"].value_counts()

eminem        1230
cold play      643
tom odell      324
ksi            318
chet faker     300
Name: artist, dtype: int64

In [222]:
lyric_df_melt.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2815 entries, 0 to 2814
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   artist  2815 non-null   object
 1   lyric   2815 non-null   object
dtypes: object(2)
memory usage: 44.1+ KB


# 3: Training the Base Classification Model
* **Tokenization and Vectorization:** For the base model have only converted the words of the lyrics to columns without taking out stop words or penalizing the frequency of the words between different artist
* **Observation:** Logistics regression performs the best on the base dataset
* **Conclusion:** Check how the models perform after removing the stop words and penalizing word frequency

In [223]:
lyric_list = list(lyric_df_melt["lyric"])
# Instantiate CountVectorizer to transform the lyrics into words and basically onehot encoding them
cv = CountVectorizer()
vectorized_corpus = cv.fit_transform(lyric_list)
df = pd.DataFrame(vectorized_corpus.todense(),columns=cv.get_feature_names())

In [224]:
lyric_df_melt["artist"].value_counts()

eminem        1230
cold play      643
tom odell      324
ksi            318
chet faker     300
Name: artist, dtype: int64

In [225]:
X = df.values
y = lyric_df_melt["artist"]
Xtrain, Xtest, ytrain, ytest = train_test_split(X,y,test_size=.20,random_state=141)
Xtrain.shape, ytrain.shape, Xtest.shape, ytest.shape

((2252, 3135), (2252,), (563, 3135), (563,))

In [226]:
# Logistics Regression model
m_lr = LogisticRegression(class_weight = "balanced")
m_lr.fit(Xtrain, ytrain)
basemodel_train_score_lr = m_lr.score(Xtrain, ytrain)
basemodel_test_score_lr = m_lr.score(Xtest,ytest)
f' train: {basemodel_train_score_lr}, test: {basemodel_test_score_lr}'

' train: 0.94449378330373, test: 0.7229129662522202'

In [227]:
# Naive Bayes classifier model
m_nb = MultinomialNB(alpha=0.06)
m_nb.fit(Xtrain,ytrain)
basemodel_train_score_nb = m_nb.score(Xtrain, ytrain)
basemodel_test_score_nb = m_nb.score(Xtest,ytest)
f' train: {basemodel_train_score_nb}, test: {basemodel_test_score_nb}'

' train: 0.9378330373001776, test: 0.6838365896980462'

In [228]:
# Random Forest classifier model
m_rf = RandomForestClassifier(n_estimators=200, # number of trees
                            max_depth=20,
                          random_state=20)
m_rf.fit(Xtrain,ytrain)
basemodel_train_score_rf = m_rf.score(Xtrain, ytrain)
basemodel_test_score_rf = m_rf.score(Xtest,ytest)
f' train: {basemodel_train_score_rf}, test: {basemodel_test_score_rf}'

' train: 0.5586145648312612, test: 0.5097690941385435'

In [229]:
#daytime
pd.DataFrame({"Model": ["Base LR Model","Base NB Model","Base RF Model"],
             "Train_Score": [round(basemodel_train_score_lr,4),round(basemodel_train_score_nb,4),round(basemodel_train_score_rf,4)],
             "Test_Score": [round(basemodel_test_score_lr,4),round(basemodel_test_score_nb,4),round(basemodel_test_score_rf,4)],
             "Description":["Starting model without removing stopwords","Starting model without removing stopwords","Starting model without removing stopwords"]})

Model  Train_Score  Test_Score  \
0  Base LR Model       0.9445      0.7229   
1  Base NB Model       0.9378      0.6838   
2  Base RF Model       0.5586      0.5098   

                                 Description  
0  Starting model without removing stopwords  
1  Starting model without removing stopwords  
2  Starting model without removing stopwords

# 4: Feature Engineering 1: Removing/ Penalizing frequent words
* **Tockenization and Vectorization:**
* **Removing common english words:** Using Count Vectorizer(stop_words="english") to remove frequent words that have little meaning
* **Penalizing frequently occuring words:** Using Term Frequency Inverse Document Frequency (TFIDF) transformer

### 4.1: Removing common english words

In [120]:
lyric_list = list(lyric_df_melt["lyric"])

In [121]:
# Instantiate CountVectorizer()
#Removes small words that are constant language-features,
#not relevant to distinguish or improving the strength of the model,
#because they recur too much in all the text.
cv = CountVectorizer(stop_words='english')
vectorized_corpus = cv.fit_transform(lyric_list)
df = pd.DataFrame(vectorized_corpus.todense(),columns=cv.get_feature_names())
df

10  100  118  15  16  18  2002  2017  2018  300  ...  yo  young  \
0      0    0    0   0   0   0     0     0     0    0  ...   0      0   
1      0    0    0   0   0   0     0     0     0    0  ...   0      0   
2      0    0    0   0   0   0     0     0     0    0  ...   0      0   
3      0    0    0   0   0   0     0     0     0    0  ...   0      0   
4      0    0    0   0   0   0     0     0     0    0  ...   1      0   
...   ..  ...  ...  ..  ..  ..   ...   ...   ...  ...  ...  ..    ...   
2810   0    0    0   0   0   0     0     0     0    0  ...   0      0   
2811   0    0    0   0   0   0     0     0     0    0  ...   0      0   
2812   0    0    0   0   0   0     0     0     0    0  ...   0      0   
2813   0    0    0   0   0   0     0     0     0    0  ...   0      0   
2814   0    0    0   0   0   0     0     0     0    0  ...   0      0   

      youngin  youth  youtube  yung  zae  zeeshan  zipped  zonin  
0           0      0        0     0    0        0       0      0  
1           0      0        0     0    0        0       0      0  
2           0      0        0     0    0        0       0      0  
3           0      0        0     0    0        0       0      0  
4           0      0        0     0    0        0       0      0  
...       ...    ...      ...   ...  ...      ...     ...    ...  
2810        0      0        0     0    0        0       0      0  
2811        0      0        0     0    0        0       0      0  
2812        0      0        0     0    0        0       0      0  
2813        0      0        0     0    0        0       0      0  
2814        0      0        0     0    0        0       0      0  

[2815 rows x 2921 columns]

### 4.2: Penalizing frequently occuring words between different artists

In [122]:
# Instantiate TfidfTransformer()
tfidf=TfidfTransformer()
tfidf_matr=tfidf.fit_transform(vectorized_corpus)
tfidf_df = pd.DataFrame(tfidf_matr.todense(),columns=cv.get_feature_names())

In [123]:
tfidf_df

10  100  118   15   16   18  2002  2017  2018  300  ...        yo  \
0     0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
1     0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
2     0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
3     0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
4     0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.459949   
...   ...  ...  ...  ...  ...  ...   ...   ...   ...  ...  ...       ...   
2810  0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
2811  0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
2812  0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
2813  0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   
2814  0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   0.0  0.0  ...  0.000000   

      young  youngin  youth  youtube  yung  zae  zeeshan  zipped  zonin  
0       0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
1       0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
2       0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
3       0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
4       0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
...     ...      ...    ...      ...   ...  ...      ...     ...    ...  
2810    0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
2811    0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
2812    0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
2813    0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  
2814    0.0      0.0    0.0      0.0   0.0  0.0      0.0     0.0    0.0  

[2815 rows x 2921 columns]

# 5: Model Training after Feature Engineering 1
* Model training after:
 * Tockenization and Vectorization
 * Removing stop words
 * Removing frequently occuring words between different artists within the dataset
* **Oberservation:** Model actually performs worst consistently across all three different models
* **Conclusion:** 
* **Try** under sampling or near miss sampling to check if this improves the model scores?
* Models might be performing worst because lyrics should be passed as a whole and not divided into different lines?
  * So when data is passed through TFIDF, it penalizes the words too much as it thinks each line belongs to different artist
  * **Try** passing entire song lyrics and checking model results


In [124]:
X = tfidf_df.values
y = lyric_df_melt["artist"]
Xtrain, Xtest, ytrain, ytest = train_test_split(X,y,test_size=.20,random_state=141)

In [125]:
Xtrain.shape, ytrain.shape, Xtest.shape, ytest.shape

((2252, 2921), (2252,), (563, 2921), (563,))

In [126]:
# Logistics Regression
m_lr = LogisticRegression()
m_lr.fit(Xtrain, ytrain)
fe1_model_train_lr = m_lr.score(Xtrain, ytrain)
fe1_model_test_lr = m_lr.score(Xtest,ytest)
f' train: {fe1_model_train_lr}, test: {fe1_model_test_lr}'

' train: 0.7713143872113677, test: 0.6731793960923623'

In [127]:
# Naive Bayes classifier model
m_nb = MultinomialNB(alpha=0.06)
m_nb.fit(Xtrain,ytrain)
fe1_model_train_nb = m_nb.score(Xtrain, ytrain)
fe1_model_test_nb = m_nb.score(Xtest,ytest)
f' train: {fe1_model_train_nb}, test: {fe1_model_test_nb}'

' train: 0.9089698046181173, test: 0.6589698046181173'

In [128]:
# Random Forest classifier model
m_rf = RandomForestClassifier(n_estimators=200, # number of trees
                            max_depth=60,
                          random_state=20)
m_rf.fit(Xtrain,ytrain)
fe1_model_train_rf = m_rf.score(Xtrain, ytrain)
fe1_model_test_rf = m_rf.score(Xtest,ytest)
f' train: {fe1_model_train_rf}, test: {fe1_model_test_rf}'

' train: 0.6936056838365897, test: 0.6092362344582594'

In [129]:
pd.DataFrame({"Model": ["Base LR Model","Base NB Model","Base RF Model", "FE1 LR Model", "FE1 NB Model", "FE1 RF Model"],
             "Train_Score": [round(basemodel_train_score_lr,4),round(basemodel_train_score_nb,4),round(basemodel_train_score_rf,4),round(fe1_model_train_lr,4),round(fe1_model_train_nb,4),round(fe1_model_train_rf,4)],
             "Test_Score": [round(basemodel_test_score_lr,4),round(basemodel_test_score_nb,4),round(basemodel_test_score_rf,4),round(fe1_model_test_lr,4),round(fe1_model_test_nb,4),round(fe1_model_test_rf,4)],
             "Description":["Starting model without removing stopwords","Starting model without removing stopwords","Starting model without removing stopwords","removing stop words and penalizing frequency","removing stop words and penalizing frequency","removing stop words and penalizing frequency"]})

Model  Train_Score  Test_Score  \
0  Base LR Model       0.9445      0.7229   
1  Base NB Model       0.9378      0.6838   
2  Base RF Model       0.5586      0.5098   
3   FE1 LR Model       0.7713      0.6732   
4   FE1 NB Model       0.9090      0.6590   
5   FE1 RF Model       0.6936      0.6092   

                                    Description  
0     Starting model without removing stopwords  
1     Starting model without removing stopwords  
2     Starting model without removing stopwords  
3  removing stop words and penalizing frequency  
4  removing stop words and penalizing frequency  
5  removing stop words and penalizing frequency

# 6: Feature Engineering 2: Class Imbalance
* Eminem covers 46.8% of the data.
* This section will resample the data to reduce the proportion of Eminem
* Taking care of class imbalance through sampling techniques:
 * Random Undersampler
 * Near Miss sampler

In [136]:
X = tfidf_df.values
y = lyric_df_melt["artist"]
Xtrain, Xtest, ytrain, ytest = train_test_split(X,y,test_size=.20,random_state=141)

In [137]:
ytrain.value_counts()

eminem        988
cold play     512
tom odell     256
ksi           248
chet faker    248
Name: artist, dtype: int64

In [138]:
rus = RandomUnderSampler(sampling_strategy={"eminem":700},random_state=10)
nm = NearMiss(sampling_strategy={"eminem": 700})

In [139]:
Xtrain_rus, ytrain_rus = rus.fit_resample(Xtrain, ytrain)
Xtrain_nm, ytrain_nm = nm.fit_resample(Xtrain, ytrain)

# 7: Model Training after Feature Engineering 2
* Model training after:
 * Taking care of class imbalance
* **Observation:** Very slight to no improvement
* **Conclusion:** Base Logistics Regression model seems to be the best model so far.
 * As discussed above trying passing the entire lyrics to TFIDF to check how model behaves

In [140]:
# Logistics Regression with random undersampler
m_lr = LogisticRegression()
m_lr.fit(Xtrain_rus, ytrain_rus)
fe2_model_train_rum_lr = m_lr.score(Xtrain_rus, ytrain_rus)
fe2_model_test_rum_lr = m_lr.score(Xtest,ytest)
f' train: {fe2_model_train_rum_lr}, test: {fe2_model_test_rum_lr}'

' train: 0.7886965376782077, test: 0.6873889875666075'

In [141]:
# Logistics Regression
m_lr = LogisticRegression()
m_lr.fit(Xtrain_nm, ytrain_nm)
fe2_model_train_nm_lr = m_lr.score(Xtrain_nm, ytrain_nm)
fe2_model_test_nm_lr = m_lr.score(Xtest,ytest)
f' train: {fe2_model_train_nm_lr}, test: {fe2_model_test_nm_lr}'

' train: 0.7953156822810591, test: 0.6838365896980462'

In [142]:
# Naive Bayes classifier model
m_nb = MultinomialNB(alpha=0.4)
m_nb.fit(Xtrain_rus, ytrain_rus)
fe2_model_train_rum_nb = m_nb.score(Xtrain_rus, ytrain_rus)
fe2_model_test_rum_nb = m_nb.score(Xtest,ytest)
f' train: {fe2_model_train_rum_nb}, test: {fe2_model_test_rum_nb}'

' train: 0.8564154786150713, test: 0.6447602131438721'

In [143]:
# Naive Bayes classifier model
m_nb = MultinomialNB(alpha=0.3)
m_nb.fit(Xtrain_nm, ytrain_nm)
fe2_model_train_nm_nb = m_nb.score(Xtrain_nm, ytrain_nm)
fe2_model_test_nm_nb = m_nb.score(Xtest,ytest)
f' train: {fe2_model_train_nm_nb}, test: {fe2_model_test_nm_nb}'

' train: 0.8742362525458248, test: 0.6571936056838366'

In [144]:
# Random Forest classifier model
m_rf = RandomForestClassifier(n_estimators=100, # number of trees
                            max_depth=40,
                          random_state=20)
m_rf.fit(Xtrain_rus,ytrain_rus)
fe2_model_train_rum_rf = m_rf.score(Xtrain_rus, ytrain_rus)
fe2_model_test_rum_rf = m_rf.score(Xtest,ytest)
f' train: {fe2_model_train_rum_rf}, test: {fe2_model_test_rum_rf}'

' train: 0.6344195519348269, test: 0.6003552397868561'

In [145]:
# Random Forest classifier model
m_rf = RandomForestClassifier(n_estimators=100, # number of trees
                            max_depth=60,
                          random_state=20)
m_rf.fit(Xtrain_nm, ytrain_nm)
fe2_model_train_nm_rf = m_rf.score(Xtrain_nm, ytrain_nm)
fe2_model_test_nm_rf = m_rf.score(Xtest,ytest)
f' train: {fe2_model_train_nm_rf}, test: {fe2_model_test_nm_rf}'

' train: 0.7067209775967414, test: 0.6412078152753108'

In [146]:
pd.DataFrame({"Model": ["Base LR Model", "FE1 LR Model","FE2 LR Model - RUM","FE2 LR Model - NM","","Base NB Model", "FE1 NB Model","FE2 NB Model - RUM","FE2 NB Model - NM","","Base RF Model", "FE1 RF Model","FE2 RF Model - RUM","FE2 RF Model - NM"],
             "Train_Score": [round(basemodel_train_score_lr,4),round(fe1_model_train_lr,4),round(fe2_model_train_rum_lr,4),round(fe2_model_train_nm_lr,4),"",round(basemodel_train_score_nb,4),round(fe1_model_train_nb,4),round(fe2_model_train_rum_nb,4),round(fe2_model_train_nm_nb,4),"",round(basemodel_train_score_rf,4),round(fe1_model_train_rf,4),round(fe2_model_train_rum_rf,4),round(fe2_model_train_nm_rf,4)],
             "Test_Score": [round(basemodel_test_score_lr,4),round(fe1_model_test_lr,4),round(fe2_model_test_rum_lr,4),round(fe2_model_test_nm_lr,4),"",round(basemodel_test_score_nb,4),round(fe1_model_test_nb,4),round(fe2_model_test_rum_nb,4),round(fe2_model_test_nm_nb,4),"",round(basemodel_test_score_rf,4),round(fe1_model_test_rf,4),round(fe2_model_test_rum_rf,4),round(fe2_model_test_nm_rf,4)],
             "Description":["Starting model without removing stopwords","removing stop words and penalizing frequency","random undersampling","near miss sampling","","Starting model without removing stopwords","removing stop words and penalizing frequency","random undersampling","near miss sampling","","Starting model without removing stopwords","removing stop words and penalizing frequency","random undersampling","near miss sampling"]})

Model Train_Score Test_Score  \
0        Base LR Model      0.9445     0.7229   
1         FE1 LR Model      0.7713     0.6732   
2   FE2 LR Model - RUM      0.7887     0.6874   
3    FE2 LR Model - NM      0.7953     0.6838   
4                                               
5        Base NB Model      0.9378     0.6838   
6         FE1 NB Model      0.9090     0.6590   
7   FE2 NB Model - RUM      0.8564     0.6448   
8    FE2 NB Model - NM      0.8742     0.6572   
9                                               
10       Base RF Model      0.5586     0.5098   
11        FE1 RF Model      0.6936     0.6092   
12  FE2 RF Model - RUM      0.6344     0.6004   
13   FE2 RF Model - NM      0.7067     0.6412   

                                     Description  
0      Starting model without removing stopwords  
1   removing stop words and penalizing frequency  
2                           random undersampling  
3                             near miss sampling  
4                                                 
5      Starting model without removing stopwords  
6   removing stop words and penalizing frequency  
7                           random undersampling  
8                             near miss sampling  
9                                                 
10     Starting model without removing stopwords  
11  removing stop words and penalizing frequency  
12                          random undersampling  
13                            near miss sampling

In [96]:
new_lyrics = ["where do we go nobody knows"]
new_lyrics_vect = cv.transform(new_lyrics).todense()
m_lr.predict(new_lyrics_vect)

# 8: Feature Engineering 3 (Passing entire lyrics) and Model Training
* Passing entire lyrics of a song to vector transformer
* **Observation:** Model scores drastically improves for all three models
* **Conclusion:** **Random forest** is the best model since it does not overfit

In [232]:
all_artist_lyric = {}
for artist,link in songs_html.items():
    artist_lyric = []
    for i in range(len(link)):
        #songs_list = []
        songs_soup = BeautifulSoup(songs_html[artist][i],'html.parser')
        songs_list = songs_soup.find_all("pre",attrs={"class":"lyric-body"})[0].text
        #songs_list = [i for i in songs_list if i != ""]
        artist_lyric.append(songs_list)
    all_artist_lyric[artist] = list(artist_lyric)

In [233]:
all_artist_lyric["eminem"][4] = ""
all_artist_lyric["eminem"][15] = ""

In [234]:
#cleaning up lines so that there are no punctuation marks and everything is lowercase
all_lyric = {}
pattern = r"[(\n)]"
pattern1 = r"[^\w\s]"
for artist,link in all_artist_lyric.items():
    all_artist_lyric_cleaned = []
    for i in range(len(link)):
        cleaned = re.sub(pattern,' ',all_artist_lyric[artist][i])
        cleaned1 = re.sub(pattern1,'',cleaned.lower())
        all_artist_lyric_cleaned.append(cleaned1)
    all_lyric[artist] = all_artist_lyric_cleaned

In [235]:
lyric_df = pd.DataFrame.from_dict(all_lyric,orient="index")
lyric_df.index.name = "artist"
lyric_df.reset_index(inplace=True)
lyric_df_melt = lyric_df.melt(id_vars="artist",var_name="index",value_name="lyric")
lyric_df_melt.drop("index",axis=1,inplace=True)
lyric_df_melt = lyric_df_melt[lyric_df_melt["lyric"].notnull()]
lyric_df_melt.reset_index(inplace=True)
lyric_df_melt.drop("index",axis=1,inplace=True)
lyric_df_melt

artist                                              lyric
0   chet faker  wont you take it all on own you feeding someth...
1    tom odell  ripples in my soups got me dreaming ten pounds...
2          ksi  yeah they cant hold us back we on another leve...
3    cold play  where do we go nobody knows ive gotta say im o...
4       eminem  yeah yo im just gonna write down my first thou...
5   chet faker  oh so your weak rhyme you doubt i bother readi...
6    tom odell  the cab is outside youve finished your beer yo...
7          ksi  randolph yeah yeah zeeshan  ah you dont like m...
8    cold play  look at the stars look how they shine for you ...
9       eminem  motherfuckers talkin crazy  yeah  sayin i shou...
10  chet faker  know i feel it in my bones i feel it take me h...
11   tom odell  dont be so hard on yourself you gave it all yo...
12         ksi  she wanna know my real name  real name  she ge...
13   cold play  i turn the music up i got my records on i shut...
14      eminem  whoa joyner joyner yeah yeah yeah yeah i done ...
15  chet faker  help me please youre breaking on my speech whi...
16   tom odell  the casino floor is full of men so frightened ...
17         ksi  drip and sip drip and sip bill up bill up bill...
18   cold play  come up to meet you tell you im sorry you dont...
19      eminem  hey em its paul um i listened to the new album...
20  chet faker  you gotta know im feeling love made of gold i ...
21   tom odell  im sick to death of eating breakfast on my own...
22   cold play  when she was just a girl she expected the worl...
23      eminem                                                   
24  chet faker  you keep on lying you keep on lying to me your...
25   tom odell  you write her a message then you press delete ...
26   cold play  i think of you i havent slept i think i do but...
27      eminem  yo how do i keep  i dont know whats up with th...
28  chet faker  i try not to reason with myself should be call...
29   tom odell  hello my beautiful friend did you get the mone...
30   cold play  the lights go out and i cant be saved tides th...
31      eminem  paul yo um so i got your message i wish you wo...
32  chet faker  im not the reason youre looking for redemption...
33   tom odell  you got the invites only late last night flowe...
34   cold play  in the darkness before the dawn in the swirlin...
35      eminem  paul yo um so i got your message i wish you wo...
36  chet faker  maybe this could be the kind of one where i si...
37   tom odell  you should look at your reflection if you wann...
38   cold play  stole a key took a car downtown where the lost...
39      eminem  its 2002 everything was totally new we were gl...
40  chet faker  over my dead body i will never shake this feel...
41   cold play  when you try your best but you dont succeed wh...
42      eminem  tay keith fck these niggas up yeah  brain dead...
43   cold play  i used to rule the world seas would rise when ...
44      eminem  okay how do i say this  fack fack fack \r last...
45   cold play  in my place in my place were lines that i coul...
46      eminem  you know everybodys been tellin me what they t...
47   cold play  ive been reading books of old the legends and ...
48      eminem  youre such a nice guy a nice guy youre faithfu...
49   cold play  cause youre a sky cause youre a sky full of st...
50      eminem  here we go again from heroes to villains used ...
51   cold play  fixing up a car to drive in it again searching...
52      eminem  i got a song filled with shit for the strong w...
53   cold play  oh i think ive landed in a world i hadnt seen ...
54      eminem                                                   
55   cold play  standing in the corner studying the lights dre...
56   cold play  oh morning come bursting the clouds amen lift ...

In [236]:
lyric_df_melt["artist"].value_counts()

cold play     18
eminem        16
chet faker    10
tom odell      9
ksi            4
Name: artist, dtype: int64

In [281]:
lyric_df_melt.drop(lyric_df_melt.index[[23,54]])

artist                                              lyric
0   chet faker  wont you take it all on own you feeding someth...
1    tom odell  ripples in my soups got me dreaming ten pounds...
2          ksi  yeah they cant hold us back we on another leve...
3    cold play  where do we go nobody knows ive gotta say im o...
4       eminem  yeah yo im just gonna write down my first thou...
5   chet faker  oh so your weak rhyme you doubt i bother readi...
6    tom odell  the cab is outside youve finished your beer yo...
7          ksi  randolph yeah yeah zeeshan  ah you dont like m...
8    cold play  look at the stars look how they shine for you ...
9       eminem  motherfuckers talkin crazy  yeah  sayin i shou...
10  chet faker  know i feel it in my bones i feel it take me h...
11   tom odell  dont be so hard on yourself you gave it all yo...
12         ksi  she wanna know my real name  real name  she ge...
13   cold play  i turn the music up i got my records on i shut...
14      eminem  whoa joyner joyner yeah yeah yeah yeah i done ...
15  chet faker  help me please youre breaking on my speech whi...
16   tom odell  the casino floor is full of men so frightened ...
17         ksi  drip and sip drip and sip bill up bill up bill...
18   cold play  come up to meet you tell you im sorry you dont...
19      eminem  hey em its paul um i listened to the new album...
20  chet faker  you gotta know im feeling love made of gold i ...
21   tom odell  im sick to death of eating breakfast on my own...
22   cold play  when she was just a girl she expected the worl...
24  chet faker  you keep on lying you keep on lying to me your...
25   tom odell  you write her a message then you press delete ...
26   cold play  i think of you i havent slept i think i do but...
27      eminem  yo how do i keep  i dont know whats up with th...
28  chet faker  i try not to reason with myself should be call...
29   tom odell  hello my beautiful friend did you get the mone...
30   cold play  the lights go out and i cant be saved tides th...
31      eminem  paul yo um so i got your message i wish you wo...
32  chet faker  im not the reason youre looking for redemption...
33   tom odell  you got the invites only late last night flowe...
34   cold play  in the darkness before the dawn in the swirlin...
35      eminem  paul yo um so i got your message i wish you wo...
36  chet faker  maybe this could be the kind of one where i si...
37   tom odell  you should look at your reflection if you wann...
38   cold play  stole a key took a car downtown where the lost...
39      eminem  its 2002 everything was totally new we were gl...
40  chet faker  over my dead body i will never shake this feel...
41   cold play  when you try your best but you dont succeed wh...
42      eminem  tay keith fck these niggas up yeah  brain dead...
43   cold play  i used to rule the world seas would rise when ...
44      eminem  okay how do i say this  fack fack fack \r last...
45   cold play  in my place in my place were lines that i coul...
46      eminem  you know everybodys been tellin me what they t...
47   cold play  ive been reading books of old the legends and ...
48      eminem  youre such a nice guy a nice guy youre faithfu...
49   cold play  cause youre a sky cause youre a sky full of st...
50      eminem  here we go again from heroes to villains used ...
51   cold play  fixing up a car to drive in it again searching...
52      eminem  i got a song filled with shit for the strong w...
53   cold play  oh i think ive landed in a world i hadnt seen ...
55   cold play  standing in the corner studying the lights dre...
56   cold play  oh morning come bursting the clouds amen lift ...

In [282]:
lyric_df_melt.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57 entries, 0 to 56
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   artist  57 non-null     object
 1   lyric   57 non-null     object
dtypes: object(2)
memory usage: 1.0+ KB


In [283]:
lyric_list = list(lyric_df_melt["lyric"])

In [284]:
cv = CountVectorizer(stop_words='english')
vectorized_corpus = cv.fit_transform(lyric_list)
df = pd.DataFrame(vectorized_corpus.todense(),columns=cv.get_feature_names())

tfidf=TfidfTransformer()
tfidf_matr=tfidf.fit_transform(vectorized_corpus)
tfidf_df = pd.DataFrame(tfidf_matr.todense(),columns=cv.get_feature_names())

In [285]:
X = tfidf_df.values
y = lyric_df_melt["artist"]
Xtrain, Xtest, ytrain, ytest = train_test_split(X,y,test_size=.20,random_state=141)
Xtrain.shape, ytrain.shape, Xtest.shape, ytest.shape

((45, 2990), (45,), (12, 2990), (12,))

In [286]:
ytrain.value_counts()

cold play     13
eminem        12
tom odell      8
chet faker     8
ksi            4
Name: artist, dtype: int64

In [287]:
# Logistics Regression
m_lr = LogisticRegression()
m_lr.fit(Xtrain, ytrain)
fe3_model_train_lr = m_lr.score(Xtrain, ytrain)
fe3_model_test_lr = m_lr.score(Xtest,ytest)
f' train: {fe3_model_train_lr}, test: {fe3_model_test_lr}'

' train: 0.8444444444444444, test: 0.75'

In [288]:
# Naive Bayes classifier model
m_nb = MultinomialNB(alpha=0.04)
m_nb.fit(Xtrain,ytrain)
fe3_model_train_nb = m_nb.score(Xtrain, ytrain)
fe3_model_test_nb = m_nb.score(Xtest,ytest)
f' train: {fe3_model_train_nb}, test: {fe3_model_test_nb}'

' train: 0.9555555555555556, test: 0.75'

In [289]:
# Random Forest classifier model
m_rf = RandomForestClassifier(n_estimators=60, # number of trees
                            max_depth=3,
                          random_state=20)
m_rf.fit(Xtrain,ytrain)
fe3_model_train_rf = m_rf.score(Xtrain, ytrain)
fe3_model_test_rf = m_rf.score(Xtest,ytest)
f' train: {fe3_model_train_rf}, test: {fe3_model_test_rf}'

' train: 0.7777777777777778, test: 0.75'

In [290]:
pd.DataFrame({"Model": ["Base LR Model", "FE1 LR Model","FE2 LR Model - RUM","FE2 LR Model - NM", "FE3 LR Model","","Base NB Model", "FE1 NB Model","FE2 NB Model - RUM","FE2 NB Model - NM", "FE3 NB Model","","Base RF Model", "FE1 RF Model","FE2 RF Model - RUM","FE2 RF Model - NM", "FE3 RF Model"],
             "Train_Score": [round(basemodel_train_score_lr,4),round(fe1_model_train_lr,4),round(fe2_model_train_rum_lr,4),round(fe2_model_train_nm_lr,4),round(fe3_model_train_lr,4),"",round(basemodel_train_score_nb,4),round(fe1_model_train_nb,4),round(fe2_model_train_rum_nb,4),round(fe2_model_train_nm_nb,4),round(fe3_model_train_nb,4),"",round(basemodel_train_score_rf,4),round(fe1_model_train_rf,4),round(fe2_model_train_rum_rf,4),round(fe2_model_train_nm_rf,4),round(fe3_model_train_rf,4)],
             "Test_Score": [round(basemodel_test_score_lr,4),round(fe1_model_test_lr,4),round(fe2_model_test_rum_lr,4),round(fe2_model_test_nm_lr,4),round(fe3_model_test_lr,4),"",round(basemodel_test_score_nb,4),round(fe1_model_test_nb,4),round(fe2_model_test_rum_nb,4),round(fe2_model_test_nm_nb,4),round(fe3_model_test_nb,4),"",round(basemodel_test_score_rf,4),round(fe1_model_test_rf,4),round(fe2_model_test_rum_rf,4),round(fe2_model_test_nm_rf,4),round(fe3_model_test_rf,4)],
             "Description":["Starting model without removing stopwords","removing stop words and penalizing frequency","random undersampling","near miss sampling","Passing entire lyrics to FE1 Model","","Starting model without removing stopwords","removing stop words and penalizing frequency","random undersampling","near miss sampling","Passing entire lyrics to FE1 Model","","Starting model without removing stopwords","removing stop words and penalizing frequency","random undersampling","near miss sampling","Passing entire lyrics to FE1 Model"]})

Model Train_Score Test_Score  \
0        Base LR Model      0.9445     0.7229   
1         FE1 LR Model      0.7713     0.6732   
2   FE2 LR Model - RUM      0.7887     0.6874   
3    FE2 LR Model - NM      0.7953     0.6838   
4         FE3 LR Model      0.8444     0.7500   
5                                               
6        Base NB Model      0.9378     0.6838   
7         FE1 NB Model      0.9090     0.6590   
8   FE2 NB Model - RUM      0.8564     0.6448   
9    FE2 NB Model - NM      0.8742     0.6572   
10        FE3 NB Model      0.9556     0.7500   
11                                              
12       Base RF Model      0.5586     0.5098   
13        FE1 RF Model      0.6936     0.6092   
14  FE2 RF Model - RUM      0.6344     0.6004   
15   FE2 RF Model - NM      0.7067     0.6412   
16        FE3 RF Model      0.7778     0.7500   

                                     Description  
0      Starting model without removing stopwords  
1   removing stop words and penalizing frequency  
2                           random undersampling  
3                             near miss sampling  
4             Passing entire lyrics to FE1 Model  
5                                                 
6      Starting model without removing stopwords  
7   removing stop words and penalizing frequency  
8                           random undersampling  
9                             near miss sampling  
10            Passing entire lyrics to FE1 Model  
11                                                
12     Starting model without removing stopwords  
13  removing stop words and penalizing frequency  
14                          random undersampling  
15                            near miss sampling  
16            Passing entire lyrics to FE1 Model

# 9: Conclusion: Pass entire lyrics to TFIDF and train on Random Forest Model!

# 10: Cross Validation of the Best Model
* Random Forest Model Cross validation
 * This provides bad results compared to the actual model since one of the artists has only 4 songs and soo the split plays a part
* Base Logistics Regression Model Cross Validation

In [291]:
cross_validation_rf = cross_val_score(estimator=m_rf, # the model to evaluate
                                     X=Xtrain,
                                     y=ytrain,
                                     scoring= "accuracy", # evaluation metrics
                                      cv=10,
                                     verbose=3) # cross validation splitting

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
C:\Users\saadv\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 4 members, which is less than n_splits=10.
  % (min_groups, self.n_splits)), UserWarning)
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s


[CV] END ................................ score: (test=0.600) total time=   0.0s
[CV] END ................................ score: (test=0.600) total time=   0.0s
[CV] END ................................ score: (test=0.400) total time=   0.0s
[CV] END ................................ score: (test=0.600) total time=   0.0s
[CV] END ................................ score: (test=0.600) total time=   0.0s
[CV] END ................................ score: (test=0.500) total time=   0.0s
[CV] END ................................ score: (test=0.500) total time=   0.0s
[CV] END ................................ score: (test=0.500) total time=   0.0s
[CV] END ................................ score: (test=0.500) total time=   0.0s
[CV] END ................................ score: (test=0.250) total time=   0.0s


[Parallel(n_jobs=1)]: Done  10 out of  10 | elapsed:    0.7s finished


In [292]:
print(f'Validation accuracy scores: {np.round(cross_validation_rf,2)}')
print(f'\nmean: {cross_validation_rf.mean():.2}')
print(f'std: {cross_validation_rf.std():.1}')

Validation accuracy scores: [0.6  0.6  0.4  0.6  0.6  0.5  0.5  0.5  0.5  0.25]

mean: 0.51
std: 0.1


In [230]:
cross_validation_rf = cross_val_score(estimator=m_lr, # the model to evaluate
                                     X=Xtrain,
                                     y=ytrain,
                                     scoring= "accuracy", # evaluation metrics
                                      cv=10,
                                     verbose=3) # cross validation splitting

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] END ................................ score: (test=0.655) total time=   1.4s


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    1.4s remaining:    0.0s


[CV] END ................................ score: (test=0.668) total time=   1.6s


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    3.1s remaining:    0.0s


[CV] END ................................ score: (test=0.680) total time=   1.4s
[CV] END ................................ score: (test=0.707) total time=   1.4s
[CV] END ................................ score: (test=0.684) total time=   1.6s
[CV] END ................................ score: (test=0.698) total time=   1.6s
[CV] END ................................ score: (test=0.636) total time=   1.5s
[CV] END ................................ score: (test=0.658) total time=   1.7s
[CV] END ................................ score: (test=0.640) total time=   1.6s
[CV] END ................................ score: (test=0.667) total time=   1.5s


[Parallel(n_jobs=1)]: Done  10 out of  10 | elapsed:   16.3s finished


In [231]:
print(f'Validation accuracy scores: {np.round(cross_validation_rf,2)}')
print(f'\nmean: {cross_validation_rf.mean():.2}')
print(f'std: {cross_validation_rf.std():.1}')

Validation accuracy scores: [0.65 0.67 0.68 0.71 0.68 0.7  0.64 0.66 0.64 0.67]

mean: 0.67
std: 0.02
